In [3]:
import pandas as pd
from transformers import AutoModelForSequenceClassification
from transformers import TrainingArguments
from transformers import AutoTokenizer
import numpy as np
from datasets import load_metric
from transformers import Trainer
from datasets import load_dataset

In [ ]:
# dataset = pd.read_csv('cleaned_fake_news_stories.csv', index_col=0)

In [40]:
raw_datasets = load_dataset("fake_news_english")

Using custom data configuration default


0 examples [00:00, ? examples/s]

ValueError: cannot convert float NaN to integer

In [39]:
dataset = load_dataset('csv', data_files='cleaned_fake_news_stories.csv', index_col=0, split='train')

Using custom data configuration default-1a41d0e223062f21
Reusing dataset csv (C:\Users\laram\.cache\huggingface\datasets\csv\default-1a41d0e223062f21\0.0.0\433e0ccc46f9880962cc2b12065189766fbb2bee57a221866138fb9203c83519)


In [38]:
dataset

Dataset({
    features: ['Unnamed: 0', 'article_content', 'fake_or_satire'],
    num_rows: 220
})

In [19]:
dataset['train'][0]

{'Unnamed: 0': 0,
 'article_content': 'Writer, Louri Michaelevitch, a former personnal assistant of the Russian President, was found dead last monday in his swiss appartment after some of the neighbors complained about the smell emanating from the residence.\n\nAccording to the city’s police departmnent, many clues collected on the site suggest that he might have been the victim of an elaborate murder plot.\n\n“The police forces have only been able to proceed to preliminary analysis before we spotted a source of radiations on the scene and had to call a decontamination team” explains Sven Munger of the Zurich Police Department.”We can confirm that the radioactive agent is a very rare russian product named TCDD Dioxin. The clues we have collected are insufficient to pronounce a definitive conclusion, but the complexity of the of plot we have exposed greatly reduces the number of suspects.”\n\nLoading...\n\nThe victim had attracted a lot of attention from the Russian government and media

In [4]:
#dataset = load_dataset('csv', data_files={'train': 'train_fake_news_stories.csv', 'test': 'test_fake_news_stories.csv'})

Using custom data configuration default-b24b2d8d0149e3d1
Reusing dataset csv (C:\Users\laram\.cache\huggingface\datasets\csv\default-b24b2d8d0149e3d1\0.0.0\433e0ccc46f9880962cc2b12065189766fbb2bee57a221866138fb9203c83519)


  0%|          | 0/2 [00:00<?, ?it/s]

In [5]:
dataset

DatasetDict({
    train: Dataset({
        features: ['article_content', 'fake_or_satire'],
        num_rows: 176
    })
    test: Dataset({
        features: ['article_content', 'fake_or_satire'],
        num_rows: 44
    })
})

In [22]:
train_dataset = dataset['train']
#test_dataset = dataset['test']

In [14]:
train_dataset[0]

{'article_content': "I just want to take a moment to give a big, warm, heartfelt thank you to secret hero Donald Trump. Shout-out to you, Donald! Nate Silver's website, FiveThirtyEight, has reported evidence that you have actually managed to stunt right-wing movements around the world just by being so shitty. The truth is startlingly clear now: You are intentionally being the world's worst leader, selflessly sacrificing your own legacy -- and indeed, your own dignity -- in order to stop the progress of the far-right and make the world a better place. And boy are you doing a great job. You are a tragic, misunderstood hero, and while history may paint you as a villain (all according to your ingenious seven-dimensional chess plan), we would like to take a moment to offer an ode to your accomplishments.\n\nNate Silver explains that there's a solid pattern evident: The warmer a foreign leadership candidate's relationship with Trump, the worse he or she has tended to do in elections. This re

In [23]:
model = AutoModelForSequenceClassification.from_pretrained("bert-base-cased", num_labels=2)

loading configuration file https://huggingface.co/bert-base-cased/resolve/main/config.json from cache at C:\Users\laram/.cache\huggingface\transformers\a803e0468a8fe090683bdc453f4fac622804f49de86d7cecaee92365d4a0f829.a64a22196690e0e82ead56f388a3ef3a50de93335926ccfa20610217db589307
Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.12.5",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 28996
}

loading weights file https://huggingface.co/bert-base-cased/resolve/main/pytorch_model.bin from c

In [24]:
tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

def tokenize_dataset(dataset,tokenizer):
    tokenized_dataset = []
    for item in dataset:
        tokenized = tokenizer(item["article_content"],padding="max_length", truncation=True)
        item.update(tokenized)
        tokenized_dataset.append(item)
    return tokenized_dataset

tokenized_train = tokenize_dataset(train_dataset,tokenizer)
#tokenized_test = tokenize_dataset(test_dataset,tokenizer)

loading configuration file https://huggingface.co/bert-base-cased/resolve/main/config.json from cache at C:\Users\laram/.cache\huggingface\transformers\a803e0468a8fe090683bdc453f4fac622804f49de86d7cecaee92365d4a0f829.a64a22196690e0e82ead56f388a3ef3a50de93335926ccfa20610217db589307
Model config BertConfig {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.12.5",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 28996
}

loading file https://huggingface.co/bert-base-cased/resolve/main/vocab.txt from cache at C:\Users

In [15]:
tokenized_train

[{'article_content': "I just want to take a moment to give a big, warm, heartfelt thank you to secret hero Donald Trump. Shout-out to you, Donald! Nate Silver's website, FiveThirtyEight, has reported evidence that you have actually managed to stunt right-wing movements around the world just by being so shitty. The truth is startlingly clear now: You are intentionally being the world's worst leader, selflessly sacrificing your own legacy -- and indeed, your own dignity -- in order to stop the progress of the far-right and make the world a better place. And boy are you doing a great job. You are a tragic, misunderstood hero, and while history may paint you as a villain (all according to your ingenious seven-dimensional chess plan), we would like to take a moment to offer an ode to your accomplishments.\n\nNate Silver explains that there's a solid pattern evident: The warmer a foreign leadership candidate's relationship with Trump, the worse he or she has tended to do in elections. This r

In [25]:
training_args = TrainingArguments("test_trainer",evaluation_strategy="epoch")

PyTorch: setting up devices
The default value for the training argument `--report_to` will change in v5 (from all installed integrations to none). In v5, you will need to use `--report_to all` to get the same behavior as now. You should start updating your code and make this info disappear :-).


In [26]:
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    metric = load_metric("accuracy")
    return metric.compute(predictions=predictions, references=labels)

In [27]:
trainer = Trainer(
    model=model, 
    args=training_args, 
    train_dataset=tokenized_train, 
    eval_dataset=tokenized_train,
    compute_metrics = compute_metrics
)

In [28]:
trainer.train()

***** Running training *****
  Num examples = 220
  Num Epochs = 3
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 8
  Gradient Accumulation steps = 1
  Total optimization steps = 84


TypeError: forward() got an unexpected keyword argument 'Unnamed: 0'

In [ ]:
trainer.evaluate(tokenized_test)

In [ ]:
predictions = trainer.predict(tokenized_test)

In [ ]:
def print_predictions_by_type(pred_type, predictions):
    print('='*200)
    print(pred_type)
    for pred in predictions:
        print(pred)

def get_predictions_by_type(dataset):
    for i,item in enumerate(dataset):
        predicted = np.argmax(predictions.predictions[i])
        gold = item['label']
        if predicted == gold: # prediction is correct
            if predicted == 1:
                print('TP: ' + item['text'])
            else:
                print('TN: ' + item['text'])
        else: # prediction is incorrect
            if predicted == 1:
                print('FP: ' + item['text'])
            else:
                print('FN: ' + item['text'])


get_predictions_by_type(test_dataset)